In [1]:
from datetime import datetime
import numpy as np
import pandas as pd
import tensorflow as tf

import sys
sys.path.append('../')

from wavy import panel
from wavy import side
from wavy import block
from wavy import nn
from wavy import plot

# Load `csv` and generate `pkl` file

In [2]:
df = pd.read_csv('../data/covid.csv')

In [3]:
df.sample(20)

Date_reported Country_code                           Country  \
95591     2020-09-19           MH                  Marshall Islands   
23131     2020-08-12           BG                          Bulgaria   
112068    2021-04-26           NG                           Nigeria   
94320     2021-04-14           ML                              Mali   
150936    2020-07-01           SD                             Sudan   
46892     2020-12-03           GQ                 Equatorial Guinea   
37480     2021-06-16           CU                              Cuba   
6454      2021-06-28           AR                         Argentina   
32873     2020-12-25           KM                           Comoros   
118306    2020-03-09           PW                             Palau   
155571    2021-01-18           TH                          Thailand   
56665     2021-05-18           GM                            Gambia   
150858    2020-04-14           SD                             Sudan   
97007     2020-07-19           MR                        Mauritania   
157982    2021-07-31           TG                              Togo   
158042    2021-09-29           TG                              Togo   
54382     2021-03-13           GF                     French Guiana   
136246    2020-09-29           VC  Saint Vincent and the Grenadines   
37465     2021-06-01           CU                              Cuba   
119347    2021-01-05           PA                            Panama   

       WHO_region  New_cases  Cumulative_cases  New_deaths  Cumulative_deaths  
95591        WPRO          0                 0           0                  0  
23131        EURO        210             13722          12                471  
112068       AFRO         35            164719           1               2062  
94320        AFRO        177             12179           3                417  
150936       EMRO        128              9500           5                592  
46892        AFRO          0              5156           0                 85  
37480        AMRO       1537            160594           8               1106  
6454         AMRO      18555           4393142         338              92317  
32873        AFRO         17               683           0                  7  
118306       WPRO          0                 0           0                  0  
155571      SEARO        369             12423           0                 70  
56665        AFRO         11              5957           0                175  
150858       EMRO         10                29           2                  4  
97007        AFRO         51              5710           1                151  
157982       AFRO        102             15624           2                152  
158042       AFRO        105             25323           1                227  
54382        AMRO         71             16764           0                 87  
136246       AMRO          0                64           0                  0  
37465        AMRO       1100            142266           8                958  
119347       AMRO       1972            253736          37               4140

In [4]:
# Remove columns
df.pop('Country_code');
df.pop('WHO_region');

# Set date as index
df = df.set_index('Date_reported')

In [5]:
df.head(20)

Country  New_cases  Cumulative_cases  New_deaths  \
Date_reported                                                         
2020-01-03     Afghanistan          0                 0           0   
2020-01-04     Afghanistan          0                 0           0   
2020-01-05     Afghanistan          0                 0           0   
2020-01-06     Afghanistan          0                 0           0   
2020-01-07     Afghanistan          0                 0           0   
2020-01-08     Afghanistan          0                 0           0   
2020-01-09     Afghanistan          0                 0           0   
2020-01-10     Afghanistan          0                 0           0   
2020-01-11     Afghanistan          0                 0           0   
2020-01-12     Afghanistan          0                 0           0   
2020-01-13     Afghanistan          0                 0           0   
2020-01-14     Afghanistan          0                 0           0   
2020-01-15     Afghanistan          0                 0           0   
2020-01-16     Afghanistan          0                 0           0   
2020-01-17     Afghanistan          0                 0           0   
2020-01-18     Afghanistan          0                 0           0   
2020-01-19     Afghanistan          0                 0           0   
2020-01-20     Afghanistan          0                 0           0   
2020-01-21     Afghanistan          0                 0           0   
2020-01-22     Afghanistan          0                 0           0   

               Cumulative_deaths  
Date_reported                     
2020-01-03                     0  
2020-01-04                     0  
2020-01-05                     0  
2020-01-06                     0  
2020-01-07                     0  
2020-01-08                     0  
2020-01-09                     0  
2020-01-10                     0  
2020-01-11                     0  
2020-01-12                     0  
2020-01-13                     0  
2020-01-14                     0  
2020-01-15                     0  
2020-01-16                     0  
2020-01-17                     0  
2020-01-18                     0  
2020-01-19                     0  
2020-01-20                     0  
2020-01-21                     0  
2020-01-22                     0

In [6]:
df_list = []
countries = df.Country.unique()
for country in countries:
    temp_df = df[df['Country']==country]
    temp_df.pop('Country')
    df_list.append(temp_df)

new_df = pd.concat(df_list, axis = 1, keys=(countries))
new_df

Afghanistan                                                \
                New_cases Cumulative_cases New_deaths Cumulative_deaths   
Date_reported                                                             
2020-01-03              0                0          0                 0   
2020-01-04              0                0          0                 0   
2020-01-05              0                0          0                 0   
2020-01-06              0                0          0                 0   
2020-01-07              0                0          0                 0   
...                   ...              ...        ...               ...   
2022-01-06             38           158245          1              7367   
2022-01-07              0           158245          0              7367   
2022-01-08              0           158245          0              7367   
2022-01-09              0           158245          0              7367   
2022-01-10            136           158381          6              7373   

                Albania                                                \
              New_cases Cumulative_cases New_deaths Cumulative_deaths   
Date_reported                                                           
2020-01-03            0                0          0                 0   
2020-01-04            0                0          0                 0   
2020-01-05            0                0          0                 0   
2020-01-06            0                0          0                 0   
2020-01-07            0                0          0                 0   
...                 ...              ...        ...               ...   
2022-01-06         1236           213257          4              3228   
2022-01-07         1648           214905          5              3233   
2022-01-08         1781           216686          0              3233   
2022-01-09         1801           218487          4              3237   
2022-01-10         1207           219694          3              3240   

                Algeria                   ...      Yemen                    \
              New_cases Cumulative_cases  ... New_deaths Cumulative_deaths   
Date_reported                             ...                                
2020-01-03            0                0  ...          0                 0   
2020-01-04            0                0  ...          0                 0   
2020-01-05            0                0  ...          0                 0   
2020-01-06            0                0  ...          0                 0   
2020-01-07            0                0  ...          0                 0   
...                 ...              ...  ...        ...               ...   
2022-01-06          462           220415  ...          1              1985   
2022-01-07          410           220825  ...          0              1985   
2022-01-08          491           221316  ...          0              1985   
2022-01-09          426           221742  ...          0              1985   
2022-01-10          415           222157  ...          1              1986   

                 Zambia                                                \
              New_cases Cumulative_cases New_deaths Cumulative_deaths   
Date_reported                                                           
2020-01-03            0                0          0                 0   
2020-01-04            0                0          0                 0   
2020-01-05            0                0          0                 0   
2020-01-06            0                0          0                 0   
2020-01-07            0                0          0                 0   
...                 ...              ...        ...               ...   
2022-01-06         8770           269991         19              3772   
2022-01-07         4096           274087         10              3782   
2022-01-08         4189           278276    

In [7]:
new_df.to_pickle("../data/covid.pkl")

# Lead `pkl` file

In [8]:
df = pd.read_pickle('../data/covid.pkl')

In [9]:
cpanel = panel.from_data(df, lookback = 5, horizon = 1, gap = 0, assets = ['Brazil', 'United States of America'], channels= ['New_cases', 'New_deaths'])

In [10]:
cpanel.plot_slider()

In [11]:
# convert to pct_change
cpanel.x = cpanel.x.side_pct_change()
cpanel.y = cpanel.y.side_pct_change()

In [12]:
# Find invalid values
print(cpanel.findna())
print(cpanel.findinf())

100%|██████████| 734/734 [00:00<00:00, 5588.38it/s]


[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80]


100%|██████████| 734/734 [00:00<00:00, 175559.94it/s]

[70, 720, 73, 75, 76, 80, 81, 82, 83, 84, 85, 721, 722, 723, 724, 725]


In [13]:
# Remove invalid values
cpanel = cpanel.dropinvalid()

100%|██████████| 734/734 [00:00<00:00, 167470.99it/s]


In [14]:
cpanel.plot_slider()

# Model

In [15]:
# Define model
model = nn.LinearRegression(cpanel)

100%|██████████| 64/64 [00:00<00:00, 123305.22it/s]
2022-01-10 23:59:58.443644: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [16]:
model.fit()

15/15 [==============================] - 1s 16ms/step - loss: 0.4169 - MAE: 0.4928 - val_loss: 23.5739 - val_MAE: 1.5434


In [17]:
predicted = model.predict()

In [18]:
model.evaluate()

2/2 [==============================] - 0s 2ms/step - loss: 4.1330 - MAE: 1.5731


[4.133019924163818, 1.5731371641159058]